### Task 1: POS Tagging
Introduction

There is an ongoing discussion whether the problem of part of speech tagging is already solved, at least for English (see Manning 2011), by reaching the tagging error rates similar or lower than the human inter-annotator agreement, which is ca. 97%. In the case of languages with rich morphology, such as Polish, there is however no doubt that the accuracies of around 91% delivered by taggers leave much to be desired and more work is needed to proclaim this task as solved.

The aim of this proposed task is therefore to stimulate research in potentially new approaches to the problem of POS tagging of Polish, which will allow to close the gap between the tagging accuracy of systems available for English and languages with rich morphology.

### Task definition
Subtask (A): Morphosyntactic disambiguation and guessing

Given a sequence of segments, each with a set of possible morphosyntactic interpretations, the goal of the task is to select the correct interpretation for each of the segments and provide an interpretation for segments for which only 'ign' interpretation has been given (segments unknown to the morphosyntactic dictionary).

### Outline:
- preprocessing danych -> tekst bez znaków interpunkcyjnych
- stworzenie embeddingów dla każdego słowa
- stworzenie miary kontekstu jako średnia ważona embeddingów w otoczeniu słowa
- k-nearest [?]

[słowo] -> [embedding] -> [disamb] -> [interpretation]

- wczytać dane tekstowe
- traktować je jak dane treningowe
- dla każdego słowa wyznaczyć klasę
- zapisać słowo z najwyższą klasyfikacją do pliku

In [3]:
### ALL IMPORTS ###
import pandas as pd
import numpy as np
import random
import matplotlib.pyplot as plt
import tensorflow as tf
from itertools import islice, chain
import re
from collections import Counter
import itertools
import time
import progressbar
from lxml import objectify, etree
from sklearn.preprocessing import LabelEncoder

In [4]:
### DATA PREPARATION ###
def read_training_data(filename):
    """Extract the first file enclosed in a tar.gz file as a list of words"""
    with open(filename) as f:
        content = f.read()
        pattern = '<\?xml version="1\.0" encoding="UTF-8"\?>\s*<\!DOCTYPE cesAna SYSTEM "xcesAnaIPI\.dtd">\s*<cesAna xmlns\:xlink="http\:\/\/www\.w3\.org\/1999\/xlink" version="1\.0" type="lex disamb">\s*<chunkList>\s*(?P<chunks>[\W\s\d\w]+)<\/chunkList>\s*<\/cesAna>'
        chunks_block = re.search(pattern, content)
        if chunks_block:
            all_chunks = chunks_block.groups('chunks')
            pattern = '<chunk type=\"s\">\s*(?P<chunk>[.\w\W\s]+?)<\/chunk>\s*'
            chunks = re.findall(pattern, all_chunks[0])
            return chunks
        return None

def create_dictionary_train(chunks):
    print("Number of chunks: {0}".format(len(chunks)))
    words = {}
    for chunk in chunks:
        pattern = '(?P<token><tok>\s*(?:[\w\W\d.]+?)<\/tok>\s*?)(?:<ns\/>)?'
        tokens = re.findall(pattern, chunk)
        for tok in tokens:
            pattern = '<orth>(?P<orth>.+)<\/orth>\s*(?:[\w\W\d.]+)'
            orth = re.search(pattern, tok)
            x = orth.group('orth')
            pattern = '<lex><base>(?P<base>.+)<\/base><ctag>(?P<ctag>.+)<\/ctag><\/lex>\s*'
            lexes = re.findall(pattern, tok)
            words[x] = [lexes]
    return words
        
    
def create_dictionary_gold(chunks):
    print("Number of chunks: {0}".format(len(chunks)))
    words = {}
    for chunk in chunks:
        pattern = '(?P<token><tok>\s*(?:[\w\W\d.]+?)<\/tok>\s*?)(?:<ns\/>)?'
        tokens = re.findall(pattern, chunk)
        for tok in tokens:
            pattern = '<orth>(?P<orth>.+)<\/orth>\s*(?:[\w\W\d.]+)'
            orth = re.search(pattern, tok)
            x = orth.group('orth')
            pattern = '<lex disamb=\"1\"><base>(?P<base>.+)<\/base><ctag>(?P<ctag>.+)<\/ctag><\/lex>\s*'
            lexes = re.findall(pattern, tok)
            words[x] = [lexes[0][1]]
    return words

def take(n, iterable):
    "Return first n items of the iterable as a list"
    return list(islice(iterable, n))

In [9]:
% time chunks = read_training_data('train-gold.xml')
% time words = create_dictionary_gold(chunks)
one_hot = LabelEncoder()
print('Data size %d' % len(words))
print("Unique words: {0}".format(len(Counter(words))))
words_sample = take(5, words)
print("\n".join(["{0} -> {1}".format(x,words[x][0]) for x in words_sample]))
chunks_train = read_training_data('train-analyzed.xml')
words_train = create_dictionary_train(chunks_train)
print('Data size %d' % len(words_train))
reference_words = list(words_train.keys()) # words list in order
chunks = pd.read_csv('pl-embeddings-skip_pure_words.txt', chunksize=1000000, delimiter=' ', header=None, encoding='utf-8')
embeddings_df = pd.DataFrame()
%time embeddings_df = pd.concat(chunk for chunk in chunks).sort_values(0)
del embeddings_df[101]
subset_of_embeddings = embeddings_df.loc[embeddings_df[0].isin(words_train.keys())]
print(len(subset_of_embeddings))
tmp = subset_of_embeddings
subset_of_embeddings['interpretation'] =  [words[word][0] for word in tmp[0]]
subset_of_embeddings['disamb'] = [False for i in range(len(subset_of_embeddings))]
word_list_with_duplicates = []
interpretation = []
disamb = []
def create_series_for_df():
    i = 0
    bar = progressbar.ProgressBar(max_value=progressbar.UnknownLength)
    #print(words_train['A'])
    print('A' in reference_words)
    for word_train in reference_words:
        try:
            #print(words_train[word_train][0])
            for k in words_train[word_train][0]: # iterate over interpretations
                #print(k[1])
                if words[word_train][0].strip() != k[1].strip(): 
                    disamb.append(0)
                else:
                    disamb.append(1)
                word_list_with_duplicates.append(word_train)
                interpretation.append(k[1])
        except:
            continue
            
        i += 1
        bar.update(i)

%time create_series_for_df()
words_count = Counter(word_list_with_duplicates)

subset_of_embeddings['Count'] = subset_of_embeddings[0].map(words_count)
subset_of_embeddings.Count = subset_of_embeddings.Count.fillna(0).astype(int)
subset_with_repetitions = pd.DataFrame(np.repeat(subset_of_embeddings.values, subset_of_embeddings['Count'].values, axis=0))
data_tuples = list(zip(word_list_with_duplicates, interpretation, disamb))
print(data_tuples[:10])
sorted_repetitions_df = subset_with_repetitions.sort([0])
data_tuples = sorted(data_tuples)
test_df = pd.DataFrame([(i[1],i[2]) for i in data_tuples], )
test_df.head()
subset_with_repetitions['interpretation'] = test_df[0]
subset_with_repetitions['disamb'] = test_df[1]
print("One-hot representation of morphosynthactic forms")
result = subset_with_repetitions
result['one_hot'] = one_hot.fit_transform(subset_with_repetitions['interpretation'])
print(result.head())
del result[101]
del result[102]
del result[103]
del result['interpretation']
tmp = result['disamb']
del result['disamb']
result = pd.concat([result, tmp],axis=1)
result.head()
with open('all_columns','w') as f:
    f.write(str(result.columns.tolist()))
    
result.to_csv('input-output-dataset.csv', encoding='utf-8')

CPU times: user 10.3 s, sys: 76 ms, total: 10.4 s
Wall time: 10.4 s
Number of chunks: 85663


KeyboardInterrupt: 

In [ ]:
### SPLIT DATA INTO TRAINING AND TEST SETS ###
correct = pd.DataFrame()
non_correct = pd.DataFrame()
correct_test = pd.DataFrame()
non_correct_test = pd.DataFrame()

bar_all = progressbar.ProgressBar(max_value=progressbar.UnknownLength)
for j, chunk in enumerate(pd.read_csv('input-output-dataset.csv', chunksize=10000)):
    del chunk['0']            
    del chunk['Unnamed: 0']
    
    if j % 5 == 0:
        correct_test = pd.concat([correct_test, chunk[chunk['disamb'] == True]])
        non_correct_test = pd.concat([non_correct_test, chunk[chunk['disamb'] == False]])
    else:
        correct = pd.concat([correct, chunk[chunk['disamb'] == True]])
        non_correct = pd.concat([non_correct, chunk[chunk['disamb'] == False]])
        bar_all.update(j)

del correct['disamb']
del non_correct['disamb']
del correct_test['disamb']
del non_correct_test['disamb']

with open('in-out_correct.csv', 'w') as f:
    correct.to_csv(f, header=False, index=False)
with open('in-out_non-correct.csv', 'w') as f:
    non_correct.to_csv(f, header=False, index=False)
with open('in-out_correct_test.csv', 'w') as f:
    correct_test.to_csv(f, header=False, index=False)
with open('in-out_non-correct_test.csv', 'w') as f:
    non_correct_test.to_csv(f, header=False, index=False)

In [ ]:
### MODEL CREATION AND TEACHING ###
def weight_variable(shape):
    initial = tf.truncated_normal(shape, stddev=0.1)
    return tf.Variable(initial)

def bias_variable(shape):
    initial = tf.constant(0.1, shape=shape)
    return tf.Variable(initial)

def add_missing_dummy_columns( d, columns ):
    missing_cols = set( columns ) - set( d.columns )
    for c in missing_cols:
        d[c] = 0

def fix_columns( d, columns ):

    add_missing_dummy_columns( d, columns )

    # make sure we have all the columns we need
    assert( set( columns ) - set( d.columns ) == set())

    extra_cols = set( d.columns ) - set( columns )
    for c in extra_cols:
        if c not in list(map(lambda x: str(x),range(0,102))):
            del d[c]
        elif c not in d:
            d[c] = 0

def create_model():
    tf.reset_default_graph()
    accu = []
    
    # first layer
    hid_layer = 140
    x = tf.placeholder(tf.float32, shape=[None, 1398])
    y_train = tf.placeholder(tf.float32, shape=[None,2])

    W_1 = weight_variable([1398, hid_layer])
    b_1 = bias_variable([hid_layer])

    h_1 = tf.nn.sigmoid(tf.add(tf.matmul(x,W_1),b_1))

    # second layer
    W_2 = weight_variable([hid_layer, 2])
    b_2 = bias_variable([2])

    h_2 =  tf.nn.sigmoid(tf.add(tf.matmul(h_1,W_2),b_2))

    # Train and evaluate the model
    cross_entropy = tf.reduce_mean(
                tf.nn.softmax_cross_entropy_with_logits(labels=y_train, logits=h_2))
    train_step = tf.train.AdamOptimizer(0.01).minimize(cross_entropy)
    correct_prediction = tf.equal(tf.argmax(h_2, 1), tf.argmax(y_train, 1))
    accuracy = tf.reduce_mean(tf.cast(correct_prediction, tf.float32))
    chunksize = 10000
    epochs = 1

    bar = progressbar.ProgressBar(max_value=epochs)

    init_op = tf.global_variables_initializer()

    # Add ops to save and restore all the variables.
    saver = tf.train.Saver()

    with tf.Session() as sess:
        sess.run(init_op)
        for i in range(epochs):
            print("Step: {0}".format(i))
            corr_chunks = pd.read_csv('in-out_correct.csv', chunksize=chunksize, delimiter=',')
            non_corr_chunks = pd.read_csv('in-out_non-correct.csv', chunksize=chunksize, delimiter=',')

            for chunk_corr, chunk_non_corr in zip(corr_chunks, non_corr_chunks):

                batch_y = pd.concat([pd.DataFrame(np.ones(len(chunk_corr))), pd.DataFrame(np.zeros(len(chunk_non_corr)))]).values
                batch_y_neg = pd.concat([pd.DataFrame(np.zeros(len(chunk_corr))), pd.DataFrame(np.ones(len(chunk_non_corr)))]).values
                batch_y = np.hstack((batch_y, batch_y_neg))

                batch_x = pd.concat([chunk_corr,chunk_non_corr], ignore_index=True)
                batch_x = batch_x.values

                #shuffle
                combined = list(zip(batch_x, batch_y))
                np.random.shuffle(combined)

                batch_x[:], batch_y[:] = zip(*combined)

                train_step.run(feed_dict={x: batch_x, y_train: batch_y})

                print("Step accuracy.")
                train_accuracy = accuracy.eval(feed_dict={
                    x: batch_x, y_train: batch_y})
                print('step {0}, train accuracy {1:.10}'.format(i, train_accuracy))
            bar.update(i)

        test_corr = pd.read_csv('in-out_correct_test.csv',chunksize=chunksize, delimiter=',')
        test_non_corr = pd.read_csv('in-out_non-correct_test.csv', chunksize=chunksize, delimiter=',')

        output = []
        for chunk_corr_tst, chunk_non_corr_tst in zip(test_corr, test_non_corr):
            test_y = pd.concat([pd.DataFrame(np.ones(len(chunk_corr_tst))), pd.DataFrame(np.zeros(len(chunk_non_corr_tst)))]).values
            test_y_neg = pd.concat([pd.DataFrame(np.zeros(len(chunk_corr_tst))), pd.DataFrame(np.ones(len(chunk_non_corr_tst)))]).values

            test_y = np.hstack((test_y, test_y_neg))

            tmp_1 = chunk_corr_tst.values
            tmp_2 = chunk_non_corr_tst.values
            test_x = np.vstack((tmp_1, tmp_2))
            accu.append(accuracy.eval(feed_dict={x: test_x, y_train: test_y}))
            print('test accuracy {0:.10f}'.format(accu[-1]))
            output.append(h_2.eval(feed_dict={x: test_x}))

        df = pd.DataFrame(output)
        df.to_csv('output_test')
        # Save the variables to disk.
        save_path = saver.save(sess, "./model.ckpt")
  `      print("Model saved in file: %s" % save_path)

In [ ]:
create_model()

In [ ]:
-

In [ ]:
### MODEL EVALUATION ON TEST DATA ###
def write_tags_input_data(test_file, output_tags):
    merged = list(itertools.chain(*output_tags))
    out = pd.DataFrame(merged)
    out.to_csv("output_tags.csv")


def check_model_unknown_output(test_file):
    tf.reset_default_graph()
    chunksize = 10000
    test = pd.read_csv(test_file,chunksize=chunksize, delimiter=',')

    # first layer
    hid_layer = 140
    x = tf.placeholder(tf.float32, shape=[None, 1398])
    y_train = tf.placeholder(tf.float32, shape=[None,2])

    W_1 = weight_variable([1398, hid_layer])
    b_1 = bias_variable([hid_layer])

    h_1 = tf.nn.sigmoid(tf.add(tf.matmul(x,W_1),b_1))

    # second layer
    W_2 = weight_variable([hid_layer, 2])
    b_2 = bias_variable([2])

    h_2 =  tf.nn.sigmoid(tf.add(tf.matmul(h_1,W_2),b_2))

    # Train and evaluate the model
    cross_entropy = tf.reduce_mean(
                tf.nn.softmax_cross_entropy_with_logits(labels=y_train, logits=h_2))
    train_step = tf.train.AdamOptimizer(0.01).minimize(cross_entropy)
    correct_prediction = tf.equal(tf.argmax(h_2, 1), tf.argmax(y_train, 1))
    accuracy = tf.reduce_mean(tf.cast(correct_prediction, tf.float32))
    chunksize = 10000
    epochs = 2

    bar = progressbar.ProgressBar(max_value=epochs)
    # Add ops to save and restore all the variables.
    saver = tf.train.Saver()

    with tf.Session() as sess:
        # Restore variables from disk.
        saver.restore(sess, "./model.ckpt")
        print("Model restored.")
        output = []
        #prepare_test_data(test_file)
        test = pd.read_csv('input_test.csv',chunksize=chunksize, delimiter=',')

        for chunk in test:
            del chunk['Unnamed: 0']
            del chunk['0']
            columns = None
            with open('all_columns') as f:
                columns = f.read().split(', ')

            fix_columns( chunk, columns )
            test_x = chunk.values
            print("Size of test_x for chunk {0}".format(len(test_x)))
            test_out = h_2.eval(feed_dict={x: test_x})
            print("Test output size: {0}".format(len(test_out)))
            output.append(test_out)

        write_tags_input_data(test_file, output)

In [ ]:
check_model_unknown_output()

In [ ]:
### CHECK IF SIZES ARE THE SAME ###
out = pd.read_csv('output_tags.csv')
input_tst = pd.read_csv('input_test.csv')
assert ( len(out) == input_tst.shape[0])
print("Length of output: {0}, shape of input data: {1}".format(len(out),input_tst.shape))

In [1]:
def get_random():
    return random.choice([True, False])

In [8]:
### TAG INPUT FILE WITH CORRECT DISAMBIGUATIONS ###
class Disambiguer():
    def __init__(self, xml):
        self.root = objectify.fromstring(xml)
        self.output = pd.read_csv('output_tags.csv').values

    def get_sentences(self):
        self.sentences = []
        self.chunks = []
        for j in self.root.chunkList.chunk:
            self.chunks.append(j.chunk)
            for i in j.chunk.tok:
                self.sentences.append(i.orth.text)
        print(' '.join(self.sentences))

        return self.chunks

    def get_ctags(self):
        self.ctags = []
        for chunk in self.root.chunkList.chunk:
            for i in chunk.tok:
                for j in i.lex:
                    self.ctags.append(j.ctag)
        return self.ctags

    def get_disambiguation(self, n, word, interpretation):
        print(word + "  " + interpretation + " " + str(n))
        if n >= len(self.output):
            return get_random()
        if float(self.output[n][0]) >= float(self.output[n][1]):
            return True
        return False

    def get_list_of_lexems(self):
        lexems = []
        ctags = self.get_ctags()
        print(len(ctags))
        for n, i in enumerate(ctags):
            lexems.append(i.getparent())
            tmp = i.getparent().getparent().orth
            orth = tmp.text
            disamb = self.get_disambiguation(n, orth, i.text)
            if disamb == True:
                i.getparent().set('disamb', str(int(disamb)))

#            if disamb == False:
#                i.getparent().getparent().remove(i.getparent())
#            else:
#                if len(i.getparent().getparent().lex) > 1:
#                    i.getparent().getparent().remove(i.getparent())
#                else:
#                    i.getparent().set('disamb', str(disamb))

        out = etree.tostring(self.root, pretty_print=True, encoding='UTF-8', xml_declaration=False)
        #out = out.encode('UTF-8')
        with open('tagged_test_file.xml', 'wb') as f:
            f.write(out)

        return lexems

class DataReader():
    def __init__(self, path):
        self.path = path

    def read_file(self):
        with open(self.path, 'rb') as f:
            content = f.read()
            return content
        return None

In [9]:
data_path = "./test-analyzed.xml"
data = DataReader(data_path)
disamb = Disambiguer(data.read_file())
#ctags = set(disamb.get_ctags())
#print("Unique ctags: {0}".format(len(ctags)))
#print(sorted(list(map(lambda x: x.text,ctags))))
disamb.get_list_of_lexems()
#for i in disamb.get_list_of_lexems():
#    print(i.attrib['disamb'])

111915
Proces  subst:sg:nom:m3 0
Proces  subst:sg:acc:m3 1
budzi  fin:sg:ter:imperf 2
wielkie  adj:sg:nom:n:pos 3
wielkie  adj:sg:acc:n:pos 4
wielkie  adj:sg:voc:n:pos 5
wielkie  adj:pl:nom:m2:pos 6
wielkie  adj:pl:acc:m2:pos 7
wielkie  adj:pl:voc:m2:pos 8
wielkie  adj:pl:nom:m3:pos 9
wielkie  adj:pl:acc:m3:pos 10
wielkie  adj:pl:voc:m3:pos 11
wielkie  adj:pl:nom:f:pos 12
wielkie  adj:pl:acc:f:pos 13
wielkie  adj:pl:voc:f:pos 14
wielkie  adj:pl:nom:n:pos 15
wielkie  adj:pl:acc:n:pos 16
wielkie  adj:pl:voc:n:pos 17
wielkie  depr:pl:nom:m2 18
wielkie  depr:pl:voc:m2 19
emocje  subst:pl:nom:f 20
emocje  subst:pl:acc:f 21
emocje  subst:pl:voc:f 22
,  interp 23
szczególnie  ign 24
wśród  prep:gen 25
szeregowych  adj:pl:gen:m1:pos 26
szeregowych  adj:pl:acc:m1:pos 27
szeregowych  adj:pl:loc:m1:pos 28
szeregowych  adj:pl:gen:m2:pos 29
szeregowych  adj:pl:loc:m2:pos 30
szeregowych  adj:pl:gen:m3:pos 31
szeregowych  adj:pl:loc:m3:pos 32
szeregowych  adj:pl:gen:f:pos 33
szeregowych  adj:pl:loc:f

A  brev:pun 1333
w  brev:pun 1334
w  prep:acc:nwok 1335
w  prep:loc:nwok 1336
w  brev:pun 1337
w  brev:pun 1338
w  brev:pun 1339
w  brev:pun 1340
w  brev:pun 1341
Gdańsku  subst:sg:loc:m3 1342
Gdańsku  subst:sg:voc:m3 1343
Gdańsku  adjp 1344
?  interp 1345
Zaledwie  comp 1346
Zaledwie  qub 1347
gdzieniegdzie  adv 1348
.  interp 1349
Przy  prep:loc 1350
Długiej  ign 1351
tylko  subst:sg:voc:f 1352
tylko  conj 1353
tylko  qub 1354
w  brev:pun 1355
w  prep:acc:nwok 1356
w  prep:loc:nwok 1357
w  brev:pun 1358
w  brev:pun 1359
w  brev:pun 1360
w  brev:pun 1361
w  brev:pun 1362
dwóch  num:pl:nom:m1:rec 1363
dwóch  num:pl:gen:m1:congr 1364
dwóch  num:pl:acc:m1:rec 1365
dwóch  num:pl:loc:m1:congr 1366
dwóch  num:pl:voc:m1:rec 1367
dwóch  num:pl:gen:m2:congr 1368
dwóch  num:pl:loc:m2:congr 1369
dwóch  num:pl:gen:m3:congr 1370
dwóch  num:pl:loc:m3:congr 1371
dwóch  num:pl:gen:f:congr 1372
dwóch  num:pl:loc:f:congr 1373
dwóch  num:pl:gen:n:congr 1374
dwóch  num:pl:loc:n:congr 1375
miejscach  subs

Nad  prep:inst:nwok 3197
Spinem  ign 3198
pojawiło  praet:sg:n:perf 3199
się  qub 3200
widmo  subst:sg:voc:f 3201
widmo  subst:sg:nom:n 3202
widmo  subst:sg:acc:n 3203
widmo  subst:sg:voc:n 3204
likwidacji  subst:sg:gen:f 3205
likwidacji  subst:sg:dat:f 3206
likwidacji  subst:sg:loc:f 3207
likwidacji  subst:pl:gen:f 3208
.  interp 3209
-  interp 3210
Dzieci  subst:pl:nom:n 3211
Dzieci  subst:pl:gen:n 3212
Dzieci  subst:pl:acc:n 3213
Dzieci  subst:pl:voc:n 3214
,  interp 3215
mając  pcon:imperf 3216
mając  pcon:imperf 3217
dobre  subst:sg:nom:n 3218
dobre  subst:sg:acc:n 3219
dobre  subst:sg:voc:n 3220
dobre  subst:pl:nom:n 3221
dobre  subst:pl:acc:n 3222
dobre  subst:pl:voc:n 3223
dobre  adj:sg:nom:n:pos 3224
dobre  adj:sg:acc:n:pos 3225
dobre  adj:sg:voc:n:pos 3226
dobre  adj:pl:nom:m2:pos 3227
dobre  adj:pl:acc:m2:pos 3228
dobre  adj:pl:voc:m2:pos 3229
dobre  adj:pl:nom:m3:pos 3230
dobre  adj:pl:acc:m3:pos 3231
dobre  adj:pl:voc:m3:pos 3232
dobre  adj:pl:nom:f:pos 3233
dobre  adj:pl:

jednego  adj:sg:gen:m1:pos 5510
jednego  adj:sg:acc:m1:pos 5511
jednego  adj:sg:gen:m2:pos 5512
jednego  adj:sg:acc:m2:pos 5513
jednego  adj:sg:gen:m3:pos 5514
jednego  adj:sg:gen:n:pos 5515
jednego  subst:sg:gen:m2 5516
jednego  subst:sg:acc:m2 5517
jednego  subst:sg:gen:n 5518
motywu  subst:sg:gen:m3 5519
,  interp 5520
jak  adv 5521
jak  adv:pos 5522
jak  conj 5523
jak  prep:nom 5524
jak  subst:sg:nom:m2 5525
jak  subst:pl:gen:f 5526
płowienie  ger:sg:nom:n:imperf:aff 5527
płowienie  ger:sg:acc:n:imperf:aff 5528
płowienie  ger:sg:nom:n:imperf:aff 5529
płowienie  ger:sg:acc:n:imperf:aff 5530
jednej  adj:sg:gen:f:pos 5531
jednej  adj:sg:dat:f:pos 5532
jednej  adj:sg:loc:f:pos 5533
barwy  subst:sg:gen:f 5534
barwy  subst:pl:nom:f 5535
barwy  subst:pl:acc:f 5536
barwy  subst:pl:voc:f 5537
barwy  subst:pl:nom:n 5538
barwy  subst:pl:acc:n 5539
barwy  subst:pl:voc:n 5540
,  interp 5541
jak  adv 5542
jak  adv:pos 5543
jak  conj 5544
jak  prep:nom 5545
jak  subst:sg:nom:m2 5546
jak  subst:pl

,  interp 7534
że  comp 7535
że  qub 7536
to  adj:sg:nom:n:pos 7537
to  adj:sg:acc:n:pos 7538
to  adj:sg:voc:n:pos 7539
to  conj 7540
to  pred 7541
to  qub 7542
to  subst:sg:nom:n 7543
to  subst:sg:acc:n 7544
co  subst:sg:nom:n 7545
co  subst:sg:gen:n 7546
co  subst:sg:dat:n 7547
co  subst:sg:acc:n 7548
co  subst:sg:inst:n 7549
co  subst:sg:loc:n 7550
co  subst:sg:voc:n 7551
co  subst:pl:nom:n 7552
co  subst:pl:gen:n 7553
co  subst:pl:dat:n 7554
co  subst:pl:acc:n 7555
co  subst:pl:inst:n 7556
co  subst:pl:loc:n 7557
co  subst:pl:voc:n 7558
co  comp 7559
co  prep:nom 7560
co  prep:acc 7561
co  qub 7562
co  subst:sg:nom:n 7563
co  subst:sg:gen:n 7564
co  subst:sg:acc:n 7565
zrobił  praet:sg:m1:perf 7566
zrobił  praet:sg:m2:perf 7567
zrobił  praet:sg:m3:perf 7568
Leszek  subst:sg:nom:m1 7569
Piotrowski  subst:sg:nom:m1 7570
Piotrowski  subst:sg:voc:m1 7571
Piotrowski  adj:sg:nom:m1:pos 7572
Piotrowski  adj:sg:voc:m1:pos 7573
Piotrowski  adj:sg:nom:m2:pos 7574
Piotrowski  adj:sg:voc:m2:po

...

Teraz  adv 102684
jest  fin:sg:ter:imperf 102685
z  brev:pun 102686
z  prep:gen:nwok 102687
z  prep:acc:nwok 102688
z  prep:inst:nwok 102689
z  qub 102690
z  brev:pun 102691
tym  adj:sg:inst:m1:pos 102692
tym  adj:sg:loc:m1:pos 102693
tym  adj:sg:inst:m2:pos 102694
tym  adj:sg:loc:m2:pos 102695
tym  adj:sg:inst:m3:pos 102696
tym  adj:sg:loc:m3:pos 102697
tym  adj:sg:inst:n:pos 102698
tym  adj:sg:loc:n:pos 102699
tym  adj:pl:dat:m1:pos 102700
tym  adj:pl:dat:m2:pos 102701
tym  adj:pl:dat:m3:pos 102702
tym  adj:pl:dat:f:pos 102703
tym  adj:pl:dat:n:pos 102704
tym  subst:sg:inst:n 102705
tym  subst:sg:loc:n 102706
tym  adv 102707
tym  conj 102708
lepiej  adv:com 102709
,  interp 102710
ale  depr:pl:nom:m2 102711
ale  depr:pl:voc:m2 102712
ale  subst:pl:nom:f 102713
ale  subst:pl:acc:f 102714
ale  subst:pl:voc:f 102715
ale  depr:pl:nom:m2 102716
ale  depr:pl:voc:m2 102717
ale  depr:pl:nom:m2 102718
ale  depr:pl:voc:m2 102719
ale  conj 102720
ale  qub 102721
było  praet:sg:n:imperf 102722
b

błyskawicznie  adv:pos 105082
wyrzuca  fin:sg:ter:imperf 105083
spod  prep:gen:nwok 105084
pancerza  subst:sg:gen:m3 105085
długą  adj:sg:acc:f:pos 105086
długą  adj:sg:inst:f:pos 105087
szyję  subst:sg:acc:f 105088
szyję  fin:sg:pri:imperf 105089
,  interp 105090
rozwiera  fin:sg:ter:imperf 105091
paszczę  subst:sg:acc:f 105092
i  brev:pun 105093
i  conj 105094
i  interj 105095
i  qub 105096
wciąga  fin:sg:ter:imperf 105097
ofiarę  subst:sg:acc:f 105098
wraz  ign 105099
ze  prep:gen:wok 105100
ze  prep:acc:wok 105101
ze  prep:inst:wok 105102
strumieniem  subst:sg:inst:m3 105103
wody  subst:sg:gen:f 105104
wody  subst:pl:nom:f 105105
wody  subst:pl:acc:f 105106
wody  subst:pl:voc:f 105107
.  interp 105108
Siła  adv 105109
Siła  num:pl:nom:m1:rec 105110
Siła  num:pl:acc:m1:rec 105111
Siła  num:pl:nom:m2:rec 105112
Siła  num:pl:acc:m2:rec 105113
Siła  num:pl:nom:m3:rec 105114
Siła  num:pl:acc:m3:rec 105115
Siła  num:pl:nom:f:rec 105116
Siła  num:pl:acc:f:rec 105117
Siła  num:pl:nom:n:rec

to  conj 107488
to  pred 107489
to  qub 107490
to  subst:sg:nom:n 107491
to  subst:sg:acc:n 107492
w  brev:pun 107493
w  prep:acc:nwok 107494
w  prep:loc:nwok 107495
w  brev:pun 107496
w  brev:pun 107497
w  brev:pun 107498
w  brev:pun 107499
w  brev:pun 107500
protokole  subst:sg:loc:m3 107501
protokole  subst:sg:voc:m3 107502
.  interp 107503
Wicemarszalek  subst:sg:nom:m1 107504
Wicemarszalek  ign 107505
Tadeusz  subst:sg:nom:m1 107506
Tadeusz  ign 107507
Rzemykowski  ign 107508
Rzemykowski  subst:sg:nom:m1 107509
:  interp 107510
Ogłaszam  fin:sg:pri:imperf 107511
dziewięciominutową  ign 107512
przerwę  subst:sg:acc:m1 107513
przerwę  subst:sg:acc:f 107514
przerwę  fin:sg:pri:perf 107515
.  interp 107516
Wicemarszalek  ign 107517
Wicemarszalek  subst:sg:nom:m1 107518
Tadeusz  subst:sg:nom:m1 107519
Tadeusz  ign 107520
Rzemykowski  subst:sg:nom:m1 107521
Rzemykowski  ign 107522
:  interp 107523
Po  subst:sg:nom:f 107524
Po  subst:sg:gen:f 107525
Po  subst:sg:dat:f 107526
Po  subst:sg

to  pred 109690
to  qub 109691
to  subst:sg:nom:n 109692
to  subst:sg:acc:n 109693
wskazanie  subst:sg:nom:n 109694
wskazanie  subst:sg:acc:n 109695
wskazanie  subst:sg:voc:n 109696
wskazanie  ger:sg:nom:n:perf:aff 109697
wskazanie  ger:sg:acc:n:perf:aff 109698
Marka  subst:sg:gen:m1 109699
Marka  subst:sg:acc:m1 109700
Marka  subst:sg:gen:m1 109701
Marka  subst:sg:acc:m1 109702
Marka  subst:sg:gen:m2 109703
Marka  subst:sg:acc:m2 109704
Marka  subst:sg:gen:m3 109705
Marka  subst:sg:nom:f 109706
Belki  depr:pl:nom:m2 109707
Belki  depr:pl:voc:m2 109708
Belki  subst:sg:gen:m1 109709
Belki  subst:sg:gen:f 109710
Belki  subst:pl:nom:f 109711
Belki  subst:pl:acc:f 109712
Belki  subst:pl:voc:f 109713
jest  fin:sg:ter:imperf 109714
obliczone  ppas:sg:nom:n:perf:aff 109715
obliczone  ppas:sg:acc:n:perf:aff 109716
obliczone  ppas:pl:nom:m2:perf:aff 109717
obliczone  ppas:pl:acc:m2:perf:aff 109718
obliczone  ppas:pl:nom:m3:perf:aff 109719
obliczone  ppas:pl:acc:m3:perf:aff 109720
obliczone  ppa

[<Element lex at 0x7f70e4ebfd08>,
 <Element lex at 0x7f70e4ebff48>,
 <Element lex at 0x7f70e4ec00c8>,
 <Element lex at 0x7f70e4ec0208>,
 <Element lex at 0x7f70e4ec02c8>,
 <Element lex at 0x7f70e4ec0388>,
 <Element lex at 0x7f70e4ec0448>,
 <Element lex at 0x7f70e4ec0508>,
 <Element lex at 0x7f70e4ec0948>,
 <Element lex at 0x7f70e4ec0988>,
 <Element lex at 0x7f70e4ec09c8>,
 <Element lex at 0x7f70e4ec0a08>,
 <Element lex at 0x7f70e4ec0a48>,
 <Element lex at 0x7f70e4ec0a88>,
 <Element lex at 0x7f70e4ec0ac8>,
 <Element lex at 0x7f70e4ec0b08>,
 <Element lex at 0x7f70e4ec0b88>,
 <Element lex at 0x7f70e4ec0c08>,
 <Element lex at 0x7f70e4ec0c88>,
 <Element lex at 0x7f70e4ec0cc8>,
 <Element lex at 0x7f70e4ec0d48>,
 <Element lex at 0x7f70e4ec0288>,
 <Element lex at 0x7f70e4ec0e48>,
 <Element lex at 0x7f70e4ec0ec8>,
 <Element lex at 0x7f70e4ec0fc8>,
 <Element lex at 0x7f70e4ec1048>,
 <Element lex at 0x7f70e4ec1088>,
 <Element lex at 0x7f70e4ec1188>,
 <Element lex at 0x7f70e4ec1208>,
 <Element lex 

In [20]:
mine = "tagged_test_file.xml"
gold = "gold-task-a-b.xml"
with open(gold, "rb") as f:
    gold_str = f.read()
with open(mine, "rb") as f:
    mine_str = f.read()
root_mine = objectify.fromstring(mine_str)
root_gold = objectify.fromstring(gold_str)

In [29]:
for chunk1, chunk2 in zip(root_mine.chunkList.chunk, root_gold.chunkList.chunk):
    for tok1 in chunk1.tok:
        print(tok1.lex.text)

None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None


None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
